In [ ]:
%pip install pyarrow
%pip install scipy

   ---------------------------------------- 0.0/41.3 MB ? eta -:--:--
   - -------------------------------------- 1.0/41.3 MB 6.3 MB/s eta 0:00:07
   -- ------------------------------------- 2.6/41.3 MB 7.2 MB/s eta 0:00:06
   ---- ----------------------------------- 4.5/41.3 MB 7.7 MB/s eta 0:00:05
   ------ --------------------------------- 6.8/41.3 MB 8.4 MB/s eta 0:00:05
   -------- ------------------------------- 8.9/41.3 MB 8.8 MB/s eta 0:00:04
   ---------- ----------------------------- 11.3/41.3 MB 9.4 MB/s eta 0:00:04
   ------------- -------------------------- 14.2/41.3 MB 10.0 MB/s eta 0:00:03
   ---------------- ----------------------- 16.5/41.3 MB 10.2 MB/s eta 0:00:03
   ------------------ --------------------- 19.4/41.3 MB 10.6 MB/s eta 0:00:03
   --------------------- ------------------ 22.0/41.3 MB 10.9 MB/s eta 0:00:02
   ------------------------ --------------- 24.9/41.3 MB 11.1 MB/s eta 0:00:02
   -------------------------- ------------- 27.8/41.3 MB 11.3 MB/s eta 0

In [ ]:
username=''
password=''

# import tqdm
import requests
import numpy as np
import json
import io
from io import BytesIO
import os
import re
import pandas as pd
from scipy.stats import pearsonr
import math
from skillcorner.client import SkillcornerClient
skillcorner=SkillcornerClient(username=username,password=password)

import pyarrow.parquet as pa



# Get Matches

In [ ]:
matches = skillcorner.get_matches()
skillcorner_matches = pd.DataFrame(matches)
skillcorner_matches.head()

id             date_time  \
0  2016339  2025-05-10T11:30:00Z   
1  2016340  2025-05-10T11:30:00Z   
2  2016423  2025-05-10T11:30:00Z   
3  2016424  2025-05-10T11:30:00Z   
4  2016425  2025-05-10T11:30:00Z   

                                       home_team  \
0        {'id': 2026, 'short_name': 'Arsenal W'}   
1        {'id': 1834, 'short_name': 'Chelsea W'}   
2      {'id': 2029, 'short_name': 'Aston Villa'}   
3          {'id': 2033, 'short_name': 'Everton'}   
4  {'id': 2031, 'short_name': 'Leicester Women'}   

                                   away_team  status  competition_id  \
0   {'id': 2027, 'short_name': 'Man Utd, W'}  closed             127   
1  {'id': 2661, 'short_name': 'Liverpool W'}  closed             127   
2     {'id': 2025, 'short_name': 'Brighton'}  closed             127   
3  {'id': 2028, 'short_name': 'Tottenham W'}  closed             127   
4     {'id': 2030, 'short_name': 'West Ham'}  closed             127   

   season_id  competition_edition_id  
0         95                     892  
1         95                     892  
2         95                     892  
3         95                     892  
4         95                     892

In [ ]:
rootDir = 'Match Events'
rootDirFailed = 'Quality Check Failed Match Events'
fileNums = []
for entry in os.scandir(rootDir):
    # print(entry.path)
    if entry.is_file():
        matchIdNum = int(entry.path.split('\\')[1].split('_')[0])
        print(matchIdNum, '\t\t', entry.path)
        fileNums.append(matchIdNum)

for entry in os.scandir(rootDirFailed):
    if entry.is_file():
        matchIdNum = int(entry.path.split('\\')[1].split('_')[0])
        print(matchIdNum, '\t\t', entry.path)
        fileNums.append(matchIdNum)

# print(fileNums)

1988084 		 Match Events\1988084_dynamic_events.csv
2000678 		 Match Events\2000678_dynamic_events.csv
2001333 		 Match Events\2001333_dynamic_events.csv
2001334 		 Match Events\2001334_dynamic_events.csv
2001335 		 Match Events\2001335_dynamic_events.csv
2001337 		 Match Events\2001337_dynamic_events.csv
2003602 		 Match Events\2003602_dynamic_events.csv
2003681 		 Match Events\2003681_dynamic_events.csv
2003682 		 Match Events\2003682_dynamic_events.csv
2005634 		 Match Events\2005634_dynamic_events.csv
2005693 		 Match Events\2005693_dynamic_events.csv
2005726 		 Match Events\2005726_dynamic_events.csv
2006145 		 Match Events\2006145_dynamic_events.csv
2007384 		 Match Events\2007384_dynamic_events.csv
2007861 		 Match Events\2007861_dynamic_events.csv
2008540 		 Match Events\2008540_dynamic_events.csv
2008601 		 Match Events\2008601_dynamic_events.csv
2008602 		 Match Events\2008602_dynamic_events.csv
2008603 		 Match Events\2008603_dynamic_events.csv
2008647 		 Match Events\2008647

In [ ]:
excluded = [1987409, 1863387, 1732596, 1728459, 1700744, 1668542, 1670500, 1508311]
rootDir = 'Match Events'
rootDirFailed = 'Quality Check Failed Match Events'
fileNums = []
# for entry in os.scandir(rootDir):
#     # print(entry.path)
#     if entry.is_file():
#         matchIdNum = int(entry.path.split('\\')[1].split('_')[0])
#         # print(matchIdNum, '\t\t', entry.path)
#         fileNums.append(matchIdNum)

# for entry in os.scandir(rootDirFailed):
#     if entry.is_file():
#         matchIdNum = int(entry.path.split('\\')[1].split('_')[0])
#         print(matchIdNum, '\t\t', entry.path)
#         fileNums.append(matchIdNum)

matchData = pd.DataFrame(columns=['id', 'home_team', 'away_team', 'home_score', 'away_score', 'pitch_length', 'pitch_width'])

for match in matches:
    dataCollection = skillcorner.get_match_data_collection(match_id=match['id'])
    curMatch = skillcorner.get_match(match_id=match['id'])
    # print(dataCollection['status'],'\n\n')
    # for i in curMatch:
    #     print(i)
    tempMatchRow = [match['id'], curMatch['home_team']['short_name'], curMatch['away_team']['short_name'], curMatch['home_team_score'], curMatch['away_team_score'], curMatch['pitch_length'], curMatch['pitch_width']]
    print(tempMatchRow)
    matchData.loc[len(matchData.index)] = tempMatchRow
    # print(match['id'], match['home_team']['short_name'], '\t', match['away_team']['short_name'], '\t', dataCollection['status'])
    # break
    # if dataCollection['status'] != 'not_available' and match['id'] not in excluded and match['id'] not in fileNums:
    #     try:
    #         dynamicEvents = skillcorner.get_dynamic_events(match_id=match['id'], params={'file_format':'csv', 'ignore_dynamic_events_check': False})
    #         dynamicEvents = pd.read_csv(BytesIO(dynamicEvents), low_memory=False)
    #         dynamicEvents.to_csv('Match Events\\' + str(match['id']) + '_dynamic_events.csv')
    #         print('Quality Check Succeeded\n\n')
    #     except:
    #         dynamicEvents = skillcorner.get_dynamic_events(match_id=match['id'], params={'file_format':'csv', 'ignore_dynamic_events_check': True})
    #         dynamicEvents = pd.read_csv(BytesIO(dynamicEvents), low_memory=False)
    #         dynamicEvents.to_csv('Quality Check Failed Match Events\\' + str(match['id']) + '_dynamic_events.csv')
    #         print('Quality Check Failed\n\n')



    # offBallRunEvents = skillcorner.get_dynamic_events_off_ball_runs(match_id=match['id'], params={'file_format':'csv', 'ignore_dynamic_events_check': True})
    # offBallRunEvents = pd.read_csv(BytesIO(offBallRunEvents))
    # dynamicPossessions = skillcorner.get_dynamic_events_player_possessions(match_id=match['id'], params={'file_format':'csv', 'ignore_dynamic_events_check': True})
    # dynamicPossessions = pd.read_csv(BytesIO(dynamicPossessions))
    # print(offBallRunEvents.head(20))
    # break


[2016339, 'Arsenal W', 'Man Utd, W', 4, 3, 105, 68]
[2016340, 'Chelsea W', 'Liverpool W', 1, 0, 103, 67]
[2016423, 'Aston Villa', 'Brighton', 3, 1, 105, 68]
[2016424, 'Everton', 'Tottenham W', 1, 1, 102, 67]
[2016425, 'Leicester Women', 'West Ham', 4, 2, 105, 68]
[2016426, 'Man City, W', 'Crystal Palace', 5, 2, 105, 68]
[2015642, 'Brighton', 'Arsenal W', 4, 2, 103, 66]
[2015253, 'West Ham', 'Aston Villa', 2, 3, 102, 64]
[2015254, 'Tottenham W', 'Chelsea W', 0, 1, 105, 68]
[2015190, 'Crystal Palace', 'Leicester Women', 2, 2, 102, 64]
[2015191, 'Liverpool W', 'Everton', 0, 2, 101, 68]
[2015255, 'Man Utd, W', 'Man City, W', 2, 2, 105, 68]
[2014147, 'Man Utd, W', 'Chelsea W', 0, 1, 105, 68]
[2014148, 'Aston Villa', 'Arsenal W', 5, 2, 105, 68]
[2013662, 'Leicester Women', 'Man City, W', 0, 1, 105, 68]
[2013663, 'Everton', 'Brighton', 2, 3, 102, 67]
[2013664, 'Crystal Palace', 'West Ham', 1, 7, 102, 64]
[2013665, 'Liverpool W', 'Tottenham W', 2, 2, 100, 68]
[2013070, 'Chelsea W', 'Crystal Pa

In [ ]:
rootDir = 'Match Events'
trackingDir = 'Tracking Data'
excludedTrackingIDs = [2009510, 1847609]
trackingFileNums = []

for entry in os.scandir(trackingDir):
    if entry.is_file():
        matchIdNum = int(entry.path.split('\\')[1].split('.')[0])
        # print(matchIdNum, '\t\t', entry.path)
        trackingFileNums.append(matchIdNum)


for i in skillcorner_matches.index:
    id = skillcorner_matches.loc[i, 'id']
    print(id)
    if id not in excludedTrackingIDs and id not in trackingFileNums:
        trackingData = skillcorner.save_match_tracking_data(id, filepath=f'Tracking Data\\' + str(id) + '.json')
        # break

2016339
2016340
2016423
2016424
2016425
2016426
2015642
2015253
2015254
2015190
2015191
2015255
2014147
2014148
2013662
2013663
2013664
2013665
2013070
2012511
2012512
2012368
2012312
2011962
2009510
2009421
2009422
2009511
2009512
2009513
2008601
2008602
2008603
2008540
2008647
2008430
2007861
2007936
2007384
2007466
2006145
2006146
2005726
2005693
2005631
2005632
2005633
2005634
2003681
2003682
2003683
2003684
2003602
2003685
2000678
2001333
2001334
2001335
2001858
2001337
1988084
1987409
1987410
1989332
1987412
1988086
1976218
1975031
1975032
1975033
1973714
1975034
1915749
1915750
1915751
1915752
1914360
1915566
1903340
1903342
1904687
1903343
1904037
1903345
1876896
1875301
1864049
1863386
1863387
1863388
1862047
1862012
1862048
1864016
1850047
1852643
1850048
1850168
1850169
1850170
1848387
1846146
1852644
1847609
1837091
1836280
1836362
1835426
1836363
1836364
1836365
1836366
1833678
1833679
1835317
1831516
1832187
1804043
1804044
1804045
1805093
1805094
1825119
1805096
1805097


In [ ]:
trackingData = skillcorner.save_match_tracking_data(id, filepath=f'Tracking Data\\' + str(id) + '.json')

# Get Carry Data
(Not used in analysis)

In [ ]:
rootDir = 'Match Events'
minumumDistanceCovered = 7.5

carryData = pd.DataFrame(columns=['Index', 'Start Time', 'End Time', 'Channel Start', 'Third Start', 'Possession Phase', 'Defensive Phase', 'Leads to Shot', 'Distance Covered', 'Progressive Distance', 'End Type', 'Number of Off Ball Runs', 'Opponents Overtaken',
                                  'T1 Runs', 'T2 Runs', 'T3 Runs', 'T4 Runs', 'T5 Runs', 'T6 Runs', 'T7 Runs', 'T8 Runs', 'T9 Runs', 'T10 Runs', 'Max Run Passing Score', 'Max Run xT', 'Total Run Passing Score', 'Total Run xT', 'Avg Run Passing Score', 'Avg Run xT'])
carryRunData = pd.DataFrame(columns=['Carry Index', 'Carry Channel Start', 'Carry Third Start', 'Carry Possession Phase', 'Carry Defensive Phase', 'Carry Leads to Shot', 'Carry Distance Covered', 'Carry Progressive Distance', 'Carry End Type',
                                     'Number of Off Ball Runs', 'Carry Opponents Overtaken', 'Run Type', 'Run Channel Start', 'Run Third Start', 'Run Distance Covered', 'Run Trajectory', 'Run Opponents Overtaken', 'Run xT', 'Run Passing Option Score'])
# carryRunData = pd.DataFrame(columns=[''])
matchData = pd.read_csv('matchData.csv')
for entry in os.scandir(rootDir):
    # print(entry.path)
    if entry.is_file():
        matchDynEvents = pd.read_csv(entry.path, low_memory=False)
        # print(matchDynEvents.head())
        obRuns = matchDynEvents.loc[matchDynEvents['event_type'] == 'off_ball_run']
        carries = matchDynEvents.loc[(matchDynEvents['carry'] == True) & (matchDynEvents['speed_avg_band_id'] >= 2) & (matchDynEvents['distance_covered'] >= minumumDistanceCovered)]# | matchDynEvents['speed_avg_band_id'] == 3)]
        # print(len(carries.index))
        for i in carries.index:
            # Wide Areas = 3
            # Half-Spaces = 2
            # Central = 1
            channelStart = 3
            if carries.loc[i, 'channel_id_start'] % 2 == 0:
                channelStart = 2
            elif carries.loc[i, 'channel_id_start'] == 3:
                channelStart = 1
            releventRuns = obRuns.loc[((obRuns['frame_start'] >= carries.loc[i, 'frame_start']) & (obRuns['frame_start'] <= carries.loc[i, 'frame_end'])) | ((obRuns['frame_end'] >= carries.loc[i, 'frame_start']) & (obRuns['frame_end'] <= carries.loc[i, 'frame_end']))]
            # print(len(releventRuns.index))

            # Progressive Distance is the difference in distance between the start/end location and the center of the opponents endline
            progressiveDistance = 0

            tempRow = [len(carryData.index), carries.loc[i, 'time_start'], carries.loc[i, 'time_end'], channelStart, carries.loc[i, 'third_id_start'], carries.loc[i, 'team_in_possession_phase_type_id'], carries.loc[i, 'team_out_of_possession_phase_type_id'], carries.loc[i, 'lead_to_shot'],
                       carries.loc[i, 'distance_covered'], progressiveDistance, int(carries.loc[i, 'end_type_id']), len(releventRuns.index), carries.loc[i, 'n_opponents_overtaken'], 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
            maxRunPOS = 0
            maxRunXT = 0
            totalRunPOS = 0
            totalRunXT = 0

            for j in releventRuns.index:
                runChannelStart = 3
                if releventRuns.loc[j, 'channel_id_start'] % 2 == 0:
                    runChannelStart = 2
                elif releventRuns.loc[j, 'channel_id_start'] == 3:
                    runChannelStart = 1
                if ('right' in carries.loc[i, 'channel_start'] and 'left' in releventRuns.loc[j, 'channel_start']) or ('left' in carries.loc[i, 'channel_start'] and 'right' in releventRuns.loc[j, 'channel_start']):
                    runChannelStart = runChannelStart * -1
                tempRunRow = [len(carryData.index), channelStart, carries.loc[i, 'third_id_start'], carries.loc[i, 'team_in_possession_phase_type_id'], carries.loc[i, 'team_out_of_possession_phase_type_id'], carries.loc[i, 'lead_to_shot'],
                       carries.loc[i, 'distance_covered'], progressiveDistance, int(carries.loc[i, 'end_type_id']), len(releventRuns.index), carries.loc[i, 'n_opponents_overtaken'], int(releventRuns.loc[j, 'event_subtype_id']), runChannelStart, releventRuns.loc[j, 'third_id_start'],
                       releventRuns.loc[j, 'distance_covered'], int(releventRuns.loc[j, 'trajectory_direction_id']), int(releventRuns.loc[j, 'n_opponents_overtaken']), releventRuns.loc[j, 'xthreat'], releventRuns.loc[j, 'passing_option_score']]
                runType = int(releventRuns.loc[j, 'event_subtype_id'])
                tempRow[12 + runType] += 1

                totalRunPOS += releventRuns.loc[j, 'passing_option_score']
                totalRunXT += releventRuns.loc[j, 'xthreat']
                if releventRuns.loc[j, 'xthreat'] > maxRunXT:
                    maxRunXT = releventRuns.loc[j, 'xthreat']
                if releventRuns.loc[j, 'passing_option_score'] > maxRunPOS:
                    maxRunPOS = releventRuns.loc[j, 'passing_option_score']

                carryRunData.loc[len(carryRunData.index)] = tempRunRow


            tempRow[23] = maxRunPOS
            tempRow[24] = maxRunXT
            tempRow[25] = totalRunPOS
            tempRow[26] = totalRunXT
            if len(releventRuns.index) > 0:
                tempRow[27] = totalRunPOS/len(releventRuns.index)
                tempRow[28] = totalRunXT/len(releventRuns.index)
            carryData.loc[len(carryData.index)] = tempRow

        # carries.to_csv('carries4.csv')
    # break
carryRunData.head(50)
carryData.to_csv('carryData.csv')
carryRunData.to_csv('carryRunData.csv')

: 

# Get Take-On Data

In [ ]:
wyscoutDataTable = pa.read_table('wyscout_events_2026.parquet')
wyscoutData = wyscoutDataTable.to_pandas()
wyscoutData.head()

sk_match_id  wy_match_id  frame  is_matched  frame_tracking_data_available  \
0      1863388      5650426  16152        True                           True   
1      1863388      5650426  17516        True                           True   
2      1863388      5650426  20342        True                           True   
3      1863388      5650426  20920       False                           True   
4      1863388      5650426  20964        True                           True   

   is_matched_applicable  aerial_duel_first_touch  aerial_duel_height  \
0                   True                     <NA>                <NA>   
1                   True                     <NA>                <NA>   
2                   True                     <NA>                <NA>   
3                   True                     <NA>                <NA>   
4                   True                     <NA>                <NA>   

   aerial_duel_opponent_height  aerial_duel_opponent_id  ... sk_team_id  \
0                         <NA>                     <NA>  ...     2029.0   
1                         <NA>                     <NA>  ...     2029.0   
2                         <NA>                     <NA>  ...     2029.0   
3                         <NA>                     <NA>  ...     2029.0   
4                         <NA>                     <NA>  ...     4109.0   

        team_name  type_primary  \
0     Aston Villa        corner   
1     Aston Villa          pass   
2     Aston Villa          pass   
3     Aston Villa          duel   
4  Crystal Palace          pass   

                                      type_secondary  video_timestamp  \
0                                             [loss]      1615.705714   
1  [back_pass, deep_completion, recovery, counter...      1751.879722   
2  [forward_pass, pass_to_final_third, recovery, ...      2034.655518   
3                      [defensive_duel, ground_duel]      2092.490713   
4               [forward_pass, short_or_medium_pass]      2096.685853   

   possession_team_id_src possession_src  possession_team_name_src  \
0                    1954             32               Aston Villa   
1                      -1             36                In Contest   
2                      -1             44                In Contest   
3                    1945             45            Crystal Palace   
4                    1945             45            Crystal Palace   

   phase_of_play_name controlled_phase_name  
0           Set Piece                  <NA>  
1           Contested                  <NA>  
2           Contested                  <NA>  
3           Set Piece                  <NA>  
4           Set Piece                  <NA>  

[5 rows x 95 columns]

In [ ]:
takeOns = wyscoutData.loc[wyscoutData['ground_duel_type'] == 'dribble']
for i in takeOns.columns.to_list():
    # print(type(i))
    print(i + ':\t\t', takeOns.loc[takeOns.index[50], i])
# print(wyscoutData['type_primary'].unique())
# print(wyscoutData['possession_team_name'].unique())

sk_match_id:		 1863388
wy_match_id:		 5650426
frame:		 40740
is_matched:		 True
frame_tracking_data_available:		 True
is_matched_applicable:		 True
aerial_duel_first_touch:		 <NA>
aerial_duel_height:		 <NA>
aerial_duel_opponent_height:		 <NA>
aerial_duel_opponent_id:		 <NA>
aerial_duel_opponent_name:		 <NA>
aerial_duel_opponent_position:		 <NA>
aerial_duel_related_duel_id:		 <NA>
carry_end_location_x:		 <NA>
carry_end_location_y:		 <NA>
carry_progression:		 nan
ground_duel_type:		 dribble
ground_duel_kept_possession:		 True
ground_duel_opponent_id:		 592208
ground_duel_opponent_name:		 I. Riley
ground_duel_opponent_position:		 RB5
ground_duel_progressed_with_ball:		 False
ground_duel_recovered_possession:		 <NA>
ground_duel_related_duel_id:		 2375586020
ground_duel_side:		 left
ground_duel_stopped_progress:		 <NA>
ground_duel_take_on:		 False
wy_event_id:		 2375586230
infraction_opponent_id:		 <NA>
infraction_opponent_name:		 <NA>
infraction_opponent_position:		 <NA>
infraction_red_car

In [ ]:
takeOnData = pd.DataFrame(columns=['Index', 'Time', 'Channel', 'Third', 'Possession Phase', 'Defensive Phase', 'Possession xG', 'Ball Kept', 'Ball Progressed', 'Number of Off Ball Runs', 'Number of Dangerous Runs',
                                  'T1 Runs', 'T2 Runs', 'T3 Runs', 'T4 Runs', 'T5 Runs', 'T6 Runs', 'T7 Runs', 'T8 Runs', 'T9 Runs', 'T10 Runs' 'Max Run Passing Score', 'Max Run xT', 'Total Run Passing Score', 'Total Run xT', 'Avg Run Passing Score', 'Avg Run xT'])
takeOnRunsData = pd.DataFrame(columns=['Take-On Index', 'Take-On Channel', 'Take-On Third', 'Take-On Possession Phase', 'Take-On Defensive Phase', 'Take-On Possession xG', 'Take-On Ball Kept', 'Take-On Ball Progressed',
                                     'Number of Off Ball Runs', 'Number of Dangerous Runs', 'Run Type', 'Run Channel', 'Run Third', 'Distance To Dribbler', 'Run Distance Covered', 'Run Trajectory', 'Run Opponents Overtaken', 'Run xT', 'Run Passing Option Score'])


matchData = pd.read_csv('matchData.csv')
for entry in os.scandir(rootDir):
    # print(entry.path)
    if entry.is_file():
        id = int(entry.path.split('\\')[1].split('_')[0])
        print('Match ID:',id)
        matchTrackingData = pd.read_json('Tracking Data\\' + str(id) + '.json')
        matchEvents = pd.read_csv(entry.path)
        curMatchTakeOns = wyscoutData.loc[(wyscoutData['sk_match_id'] == id) & (wyscoutData['ground_duel_type'] == 'dribble')]
        # curMatchTakeOns.to_csv('_' + str(id) + 'TakeOns.csv')
        curMatchData = matchData.loc[matchData['id'] == id]
        pitchLen = curMatchData.loc[curMatchData.index[0], 'pitch_length']
        pitchWidth = curMatchData.loc[curMatchData.index[0], 'pitch_width']
        print('Num of Take-Ons this Game:', len(curMatchTakeOns.index))
        for i in curMatchTakeOns.index:
            print('\n')
            channel = 0
            third = 0
            curFrame = curMatchTakeOns.loc[i, 'frame']
            print('Match ID:',id)
            print('Current Frame:', curFrame)
            print('Player ID:', int(curMatchTakeOns.loc[i, 'sk_player_id']))
            print('Player Name:', curMatchTakeOns.loc[i, 'player_name'])
            curFramePlayerPossession = matchEvents.loc[(matchEvents['event_type'] == 'player_possession') & (matchEvents['frame_start'] <= curFrame) & (matchEvents['player_id'] == int(curMatchTakeOns.loc[i, 'sk_player_id']))]
            if len(curFramePlayerPossession.index) == 0:
                continue
            curFramePlayerPossessionIndex = curFramePlayerPossession.index[len(curFramePlayerPossession.index)-1]
            posPhase = curFramePlayerPossession.loc[curFramePlayerPossessionIndex, 'team_in_possession_phase_type_id']
            defPhase = curFramePlayerPossession.loc[curFramePlayerPossessionIndex, 'team_out_of_possession_phase_type_id']
            curPossessionEventID = curFramePlayerPossession.loc[curFramePlayerPossessionIndex, 'event_id']
            curOffBallRuns = matchEvents.loc[(matchEvents['event_type'] == 'off_ball_run') & (matchEvents['associated_player_possession_event_id'] == curPossessionEventID)]
            leftToRight = curFramePlayerPossession.loc[curFramePlayerPossessionIndex, 'attacking_side_id']

            print('Possession Event ID:',curPossessionEventID)

            dribblerPlayerID = int(curMatchTakeOns.loc[i, 'sk_player_id'])
            dribblerX = -1
            dribblerY = -1
            playerLocationData = matchTrackingData.loc[curFrame, 'player_data']
            for j in playerLocationData:
                if j['player_id'] == dribblerPlayerID:
                    dribblerX = j['x']
                    dribblerY = j['y']
                    if leftToRight == 1:
                        if dribblerX >= pitchLen/6:
                            third = 3
                        elif dribblerX >= -pitchLen/6:
                            third = 2
                        else:
                            third = 1
                    else:
                        if dribblerX > pitchLen/6:
                            third = 1
                        elif dribblerX > -pitchLen/6:
                            third = 2
                        else:
                            third = 3
                    if abs(dribblerY) >= 22:
                        channel = 3
                    elif abs(dribblerY) >= 10:
                        channel = 2
                    else:
                        channel = 1
                    # break
            print('Number of Off Ball Runs:',len(curOffBallRuns.index))
            dangerousRuns = 0
            for j in curOffBallRuns.index:
                if curOffBallRuns.loc[j, 'dangerous'] == True:
                    # print('Dangerous Runs',curOffBallRuns.loc[j, 'dangerous'])
                    dangerousRuns += 1
            print('Number of Dangerous Runs:', dangerousRuns)
            tempTakeOn = [len(takeOnData.index), curMatchTakeOns.loc[i, 'timestamp'], channel, third, posPhase, defPhase, curMatchTakeOns.loc[i, 'possession_attack_xg'], curMatchTakeOns.loc[i, 'ground_duel_kept_possession'], curMatchTakeOns.loc[i, 'ground_duel_progressed_with_ball'],
                          len(curOffBallRuns.index), dangerousRuns, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]

            for j in curOffBallRuns.index:
                runThird = 0
                runChannel = 0
                distanceToDribbler = -1
                runnerID = int(curOffBallRuns.loc[j, 'player_id'])
                runnerX = -1
                runnerY = -1
                if dribblerX != -1:
                    for k in playerLocationData:
                        if k['player_id'] == runnerID:
                            runnerX = k['x']
                            runnerY = k['y']
                            if leftToRight == 1:
                                if runnerX >= pitchLen/6:
                                    runThird = 3
                                elif runnerX >= -pitchLen/6:
                                    runThird = 2
                                else:
                                    runThird = 1
                            else:
                                if runnerX > pitchLen/6:
                                    runThird = 1
                                elif runnerX > -pitchLen/6:
                                    runThird = 2
                                else:
                                    runThird = 3
                            if abs(runnerY) >= 22:
                                runChannel = 3
                            elif abs(runnerY) >= 10:
                                runChannel = 2
                            else:
                                runChannel = 1
                            if runnerY * dribblerY < 0 and runChannel > 1:
                                runChannel = -runChannel
                            # break
                if dribblerX != -1 and runnerX != -1:
                    # Find the distance between them
                    distanceToDribbler = math.sqrt(((dribblerX - runnerX) * (dribblerX - runnerX)) + ((dribblerY - runnerY) * (dribblerY - runnerY)))
                    print(runnerX, runnerY, '\t\t\t', dribblerX, dribblerY)

                tempTakeOn[10 + int(curOffBallRuns.loc[j, 'event_subtype_id'])] += 1
                tempRun = [len(takeOnData.index), channel, third, int(posPhase), int(defPhase), float(curMatchTakeOns.loc[i, 'possession_attack_xg']), curMatchTakeOns.loc[i, 'ground_duel_kept_possession'], curMatchTakeOns.loc[i, 'ground_duel_progressed_with_ball'],
                          len(curOffBallRuns.index), int(dangerousRuns), int(curOffBallRuns.loc[j, 'event_subtype_id']), runChannel, runThird, distanceToDribbler, curOffBallRuns.loc[j, 'distance_covered'], int(curOffBallRuns.loc[j, 'trajectory_direction_id']),
                          int(curOffBallRuns.loc[j, 'n_opponents_overtaken']), curOffBallRuns.loc[j, 'xthreat'], curOffBallRuns.loc[j, 'passing_option_score']]
                print(tempRun)
                takeOnRunsData.loc[len(takeOnRunsData.index)] = tempRun
            takeOnData.loc[len(takeOnData.index)] = tempTakeOn
    # break
# print(curMatchTakeOns.loc[12449, 'timestamp'])
# for i in curMatchTakeOns.columns:
#     print(i, curMatchTakeOns.loc[15270,i])
takeOnData.to_csv('takeOnData.csv')
takeOnRunsData.to_csv('takeOnRunsData.csv')

Match ID: 1448682
Num of Take-Ons this Game: 47


Match ID: 1448682
Current Frame: 33723
Player ID: 815170
Player Name: H. Hershfelt
Possession Event ID: 8_540
Number of Off Ball Runs: 1
Number of Dangerous Runs: 0
-6.05 15.11 			 -10.22 5.89
[0, 1, 2, 5, 5, 0.0, np.True_, np.False_, 1, 0, 6, 2, 2, 10.11915510307061, np.float64(8.77), 4, 3, np.float64(0.0052), np.float64(0.7671)]


Match ID: 1448682
Current Frame: 41180
Player ID: 62527
Player Name: A. Hatch
Possession Event ID: 8_689
Number of Off Ball Runs: 0
Number of Dangerous Runs: 0


Match ID: 1448682
Current Frame: 18785
Player ID: 22385
Player Name: Ji So-Yun
Possession Event ID: 8_341
Number of Off Ball Runs: 0
Number of Dangerous Runs: 0


Match ID: 1448682
Current Frame: 3430
Player ID: 815169
Player Name: K. Wiesner
Possession Event ID: 8_40
Number of Off Ball Runs: 0
Number of Dangerous Runs: 0


Match ID: 1448682
Current Frame: 52351
Player ID: 62668
Player Name: O. Sarr
Possession Event ID: 8_861
Number of Off Ball Runs

C:\Users\adame\AppData\Local\Temp\ipykernel_39040\2511278623.py:14: DtypeWarning: Columns (277) have mixed types. Specify dtype option on import or set low_memory=False.
  matchEvents = pd.read_csv(entry.path)


Num of Take-Ons this Game: 65


Match ID: 1455157
Current Frame: 14293
Player ID: 57125
Player Name: Y. Nagasato
Possession Event ID: 8_226
Number of Off Ball Runs: 0
Number of Dangerous Runs: 0


Match ID: 1455157
Current Frame: 2142
Player ID: 301631
Player Name: E. Bahr
Possession Event ID: 8_42
Number of Off Ball Runs: 2
Number of Dangerous Runs: 1
35.94 -22.21 			 36.44 -28.36
[94, 3, 3, 2, 8, 0.0, np.True_, np.False_, 2, 1, 10, 3, 3, 6.170291727301067, np.float64(30.65), 1, 8, np.float64(0.0162), np.float64(0.9655)]
32.58 7.59 			 36.44 -28.36
[94, 3, 3, 2, 8, 0.0, np.True_, np.False_, 2, 1, 3, -1, 3, 36.156632863141446, np.float64(6.79), 1, 0, np.float64(0.0661), np.float64(0.6611)]


Match ID: 1455157
Current Frame: 61018
Player ID: 633812
Player Name: K. Fischer
Possession Event ID: 8_828
Number of Off Ball Runs: 1
Number of Dangerous Runs: 0
-35.24 -30.63 			 -31.75 -24.12
[95, 3, 3, 5, 5, 0.0, np.True_, np.True_, 1, 0, 5, 3, 3, 7.386487663294375, np.float64(12.86), 1, 2, np.

C:\Users\adame\AppData\Local\Temp\ipykernel_39040\2511278623.py:14: DtypeWarning: Columns (253,254,255) have mixed types. Specify dtype option on import or set low_memory=False.
  matchEvents = pd.read_csv(entry.path)


Num of Take-Ons this Game: 46


Match ID: 1459805
Current Frame: 47001
Player ID: 617127
Player Name: H. Hopkins
Possession Event ID: 8_675
Number of Off Ball Runs: 2
Number of Dangerous Runs: 2
32.69 0.46 			 46.72 11.99
[266, 2, 3, 4, 11, 0.11699999868869781, np.True_, np.False_, 2, 2, 9, 1, 3, 18.159895374147947, np.float64(21.96), 1, -1, np.float64(0.0747), np.float64(0.6892)]
34.06 -13.62 			 46.72 11.99
[266, 2, 3, 4, 11, 0.11699999868869781, np.True_, np.False_, 2, 2, 3, -2, 3, 28.568298864300615, np.float64(14.85), 1, -1, np.float64(0.0819), np.float64(0.9139)]


Match ID: 1459805
Current Frame: 44116
Player ID: 63543
Player Name: B. St-Georges
Possession Event ID: 8_639
Number of Off Ball Runs: 0
Number of Dangerous Runs: 0


Match ID: 1459805
Current Frame: 29482
Player ID: 75099
Player Name: A. Sanchez
Possession Event ID: 8_437
Number of Off Ball Runs: 0
Number of Dangerous Runs: 0


Match ID: 1459805
Current Frame: 25121
Player ID: 162041
Player Name: F. Tagliaferri
Posses

...

Num of Take-Ons this Game: 35


Match ID: 2015253
Current Frame: 36642
Player ID: 62646
Player Name: E. Salmon
Possession Event ID: 8_651
Number of Off Ball Runs: 0
Number of Dangerous Runs: 0


Match ID: 2015253
Current Frame: 20218
Player ID: 22574
Player Name: K. Gorry
Possession Event ID: 8_422
Number of Off Ball Runs: 1
Number of Dangerous Runs: 1
-22.66 1.56 			 -17.29 17.25
[11150, 2, 3, 3, 12, 0.7623000144958496, np.True_, np.True_, 1, 1, 8, 1, 3, 16.58351591189275, np.float64(25.48), 1, 2, np.float64(0.0617), np.float64(0.9643)]


Match ID: 2015253
Current Frame: 30283
Player ID: 62646
Player Name: E. Salmon
Possession Event ID: 8_595
Number of Off Ball Runs: 3
Number of Dangerous Runs: 1
0.03 16.91 			 11.16 19.23
[11151, 2, 2, 1, 9, nan, np.True_, np.True_, 3, 1, 1, 2, 2, 11.369226007077176, np.float64(15.2), 1, 3, np.float64(0.0176), np.float64(0.9259)]
13.51 1.85 			 11.16 19.23
[11151, 2, 2, 1, 9, nan, np.True_, np.True_, 3, 1, 9, 1, 2, 17.53815554726323, np.float64(10.28

C:\Users\adame\AppData\Local\Temp\ipykernel_39040\2511278623.py:14: DtypeWarning: Columns (277) have mixed types. Specify dtype option on import or set low_memory=False.
  matchEvents = pd.read_csv(entry.path)


Num of Take-Ons this Game: 34


Match ID: 2015254
Current Frame: 6571
Player ID: 52565
Player Name: C. Macário
Possession Event ID: 8_120
Number of Off Ball Runs: 2
Number of Dangerous Runs: 1
17.24 20.57 			 19.5 22.52
[11184, 3, 3, 2, 8, 0.0, np.True_, np.False_, 2, 1, 8, 2, 2, 2.9849790619031156, np.float64(17.4), 1, 2, np.float64(0.018), np.float64(0.847)]
16.21 -11.79 			 19.5 22.52
[11184, 3, 3, 2, 8, 0.0, np.True_, np.False_, 2, 1, 8, -2, 2, 34.46737878052232, np.float64(6.5), 1, 2, np.float64(0.0336), np.float64(0.9366)]


Match ID: 2015254
Current Frame: 26311
Player ID: 52565
Player Name: C. Macário
Possession Event ID: 8_436
Number of Off Ball Runs: 3
Number of Dangerous Runs: 2
36.63 -11.25 			 43.83 25.84
[11185, 3, 3, 3, 12, 0.0, np.True_, np.True_, 3, 2, 3, -2, 3, 37.782378167606126, np.float64(16.08), 1, 0, np.float64(0.0212), np.float64(0.6627)]
40.02 1.8 			 43.83 25.84
[11185, 3, 3, 3, 12, 0.0, np.True_, np.True_, 3, 2, 3, 1, 3, 24.340043138827834, np.float64(5.32), 

C:\Users\adame\AppData\Local\Temp\ipykernel_39040\2511278623.py:14: DtypeWarning: Columns (265) have mixed types. Specify dtype option on import or set low_memory=False.
  matchEvents = pd.read_csv(entry.path)


Num of Take-Ons this Game: 31


Match ID: 2015255
Current Frame: 1923
Player ID: 57070
Player Name: L. Hemp
Possession Event ID: 8_34
Number of Off Ball Runs: 1
Number of Dangerous Runs: 0
29.36 -19.79 			 26.54 -22.22
[11218, 3, 1, 5, 5, 0.0, np.True_, np.True_, 1, 0, 8, 2, 1, 3.7225394558016442, np.float64(19.87), 1, 2, np.float64(0.0137), np.float64(0.8756)]


Match ID: 2015255
Current Frame: 16087
Player ID: 22604
Player Name: A. Greenwood
Possession Event ID: 8_202
Number of Off Ball Runs: 0
Number of Dangerous Runs: 0


Match ID: 2015255
Current Frame: 28357
Player ID: 57076
Player Name: J. Park
Possession Event ID: 8_390
Number of Off Ball Runs: 0
Number of Dangerous Runs: 0


Match ID: 2015255
Current Frame: 31091
Player ID: 68416
Player Name: K. Casparij
Possession Event ID: 8_429
Number of Off Ball Runs: 2
Number of Dangerous Runs: 2
-14.94 17.34 			 -5.68 34.25
[11221, 3, 2, 2, 8, 0.0, np.True_, np.True_, 2, 2, 1, 2, 2, 19.27941129806613, np.float64(11.1), 1, 1, np.float64(0